In [1]:
from IPython.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

import numpy as np
from bokeh.plotting import figure, show, output_file, save
from bokeh.palettes import Viridis, Category10, Category20
from bokeh.layouts import gridplot
from bokeh.io import output_notebook
output_notebook()

from neuromod.utils import plot_lines, plot_weight_ev, load_results, plot_control, plot_net_reward

Loading BokehJS ...

ModuleNotFoundError: No module named 'neuromod'

In [2]:
# results_path = "../results/non_linear_correlated_gaussian_26-10-2022_12-26-12-997"
# results_path = "../results/non_linear_4D_gaussian_26-10-2022_13-03-56-743"
# results_path = "../results/non_linear_correlated_gaussian_long_26-10-2022_14-01-50-249"
# results_path = "../results/non_linear_4D_gaussian_long_26-10-2022_14-00-04-207"
# results_path = "../results/non_linear_correlated_gaussian_long_300_26-10-2022_15-55-55-095"
# results_path = "../results/non_linear_4D_gaussian_long_300_26-10-2022_15-55-44-044"
results_path = "../results/test_linear_net_04-11-2022_17-53-12-769"

In [3]:
params, results = load_results(results_path)

In [4]:
params.keys()

dict_keys(['dataset_params', 'model_params', 'equation_params', 'control_params', 'reset_model_params'])

In [7]:
results.keys()

dict_keys(['iters', 'Loss_t_sim', 'weights_sim', 'weights_iters_sim', 'time_span', 'W1_t_eq', 'W2_t_eq', 'Loss_t_eq', 'W1_t_control_init', 'W2_t_control_init', 'Loss_t_control_init', 'control_signal_init', 'cumulated_reward_opt', 'W1_t_control_opt', 'W2_t_control_opt', 'Loss_t_control_opt', 'control_signal', 'Loss_t_sim_OPT', 'weights_sim_OPT', 'weights_iters_sim_OPT', 'iters_OPT'])

In [5]:
iters, loss, Loss_t, Loss_t_control = results["iters"], results["Loss_t_sim"], results["Loss_t_eq"], results["Loss_t_control_init"]

In [6]:
losses = (loss, Loss_t, Loss_t_control)
colors = (Category10[10][0], Category10[10][0], Category10[10][1])
legends = ("Real Non-linear", "Approximation", "Init Control")
alphas = (0.3, 1, 1)

s = plot_lines(iters, losses, legends, alphas, colors)
show(s)

In [58]:
weights = results["weights_sim"]

In [59]:
W1_t, W2_t = results["W1_t_eq"], results["W2_t_eq"] 
weights_iter = results["weights_iters_sim"]

In [60]:
flat_W1_t = np.reshape(weights[0], (weights[0].shape[0], -1))
flat_eq_W1_t = np.reshape(W1_t, (W1_t.shape[0], -1))

flat_W2_t = np.reshape(weights[1], (weights[1].shape[0], -1))
flat_eq_W2_t = np.reshape(W2_t, (W2_t.shape[0], -1))

weight_plot1 = plot_weight_ev(flat_W1_t, flat_eq_W1_t, sim_iters=weights_iter, eq_iters=iters, title="W1")
weight_plot2 = plot_weight_ev(flat_W2_t, flat_eq_W2_t, sim_iters=weights_iter, eq_iters=iters, title="W2")
grid = gridplot([weight_plot1, weight_plot2], ncols=2, width=600, height=500)
show(grid)

In [61]:
iter_control = params["control_params"]["iters_control"]
cumulated_reward = results["cumulated_reward_opt"]
opt = plot_lines(np.arange(iter_control), (cumulated_reward,), x_axis_label="gradient steps on control", y_axis_label="Cumulated reward")
show(opt)

In [62]:
W1_t_opt, W2_t_opt, Loss_t_opt = results["W1_t_control_opt"], results["W2_t_control_opt"], results["Loss_t_control_opt"]

In [63]:
losses = (loss, Loss_t, Loss_t_opt)
colors = (Category10[10][0], Category10[10][0], Category10[10][1])
legends = ("Real Non-linear", "Approximation", "Approximated Optimized Control")
alphas = (0.3, 1, 1)

s = plot_lines(iters, losses, legends, alphas, colors)
show(s)

In [64]:
loss_OPT = results["Loss_t_sim_OPT"]

In [65]:
G1_tilda, G2_tilda = results["control_signal"]
G1_tilda, G2_tilda = G1_tilda.detach().cpu().numpy(), G2_tilda.detach().cpu().numpy()
G1_t = G1_tilda - np.ones(G1_tilda.shape)
G2_t = G2_tilda - np.ones(G2_tilda.shape)

flat_G1_t = np.reshape(G1_t, (G1_t.shape[0], -1))
flat_G2_t = np.reshape(G2_t, (G2_t.shape[0], -1))

In [66]:
control_1 = plot_control(flat_G1_t, eq_iters=iters, title="G1")
control_2 = plot_control(flat_G2_t, eq_iters=iters, title="G2")
grid = gridplot([control_1, control_2], ncols=2, width=600, height=500)
show(grid)

In [67]:
losses = (loss, Loss_t, Loss_t_opt, loss_OPT)
colors = (Category10[10][0], Category10[10][0], Category10[10][1], Category10[10][1])
legends = ("Real Non-linear", "Approximation", "Approximated Optimized Control", "Optimized Non-linear")
alphas = (0.3, 1, 1, 0.3)

s = plot_lines(iters, losses, legends, alphas, colors)
show(s)

In [68]:
cost_coef = params["control_params"]["cost_coef"]
reward_convertion = params["control_params"]["reward_convertion"]

control_cost = np.exp(cost_coef*(np.sum(G1_t**2, axis=(-1, -2)) + np.sum(G2_t**2, axis=(-1, -2)))) - 1
baseline_control_cost = np.zeros(control_cost.shape)

colors = (Category10[10][0], Category10[10][1])
losses = (loss, loss_OPT)
control_costs = (baseline_control_cost, control_cost)
legends = ("Baseline", "Training with control")

In [69]:
s, net_rewards, offset = plot_net_reward(iters, losses, control_costs, reward_convertion, labels=legends, colors=colors)
show(s)